## Open Street Maps - OSM

OpenStreetMap is a free, editable map of the whole world that is being built by volunteers largely from scratch and released with an open-content license.
From this source, one can download Points of Interest (POIs) like schools, hospitals, churchs, etc. Also, the entire road network of a city can be downloaded. 
[Source](https://wiki.openstreetmap.org/wiki/About_OpenStreetMap#:~:text=OpenStreetMap%20is%20a%20free%2C%20editable,of%20our%20underlying%20map%20data.).

OSM has an API for accessing their data. However, this course uses [OSMnx](https://geoffboeing.com/publications/osmnx-paper/), a Python package that simplifies the querying process. 



### Downloading POIs
OSMnx has the feature module that downloads OpenStreetMap geospatial features’ geometries and attributes.
>Retrieve points of interest, building footprints, transit lines/stops, or any other map features from OSM, including their geometries and attribute data, then construct a GeoDataFrame of them. You can use this module to query for nodes, ways, and relations (the latter of type “multipolygon” or “boundary” only) by passing a dictionary of desired OSM tags.

According to the [documentation](https://osmnx.readthedocs.io/en/stable/user-reference.html#osmnx.features.features_from_bbox), the tags should be specified as follows:
>**tags** (dict) – Dict of tags used for finding elements in the selected area. Results returned are the union, not intersection of each individual tag. Each result matches at least one given tag. The dict keys should be OSM tags, (e.g., building, landuse, highway, etc) and the dict values should be either True to retrieve all items with the given tag, or a string to get a single tag-value combination, or a list of strings to get multiple values for the given tag. For example, tags = {‘building’: True} would return all building footprints in the area. tags = {‘amenity’:True, ‘landuse’:[‘retail’,’commercial’], ‘highway’:’bus_stop’} would return all amenities, landuse=retail, landuse=commercial, and highway=bus_stop.


#### Download Hospitals
In order to download all POIs specified as hospitals, one would do the following:

In [ ]:
# !pip install geopandas osmnx folium

import osmnx as ox
import geopandas as gpd
from shapely import Point, Polygon
import folium

In [31]:
# Obtain the Area of Interest
d = {'name': ['epicenter'], 'geometry': [Point(37.196, 38.011)]}
gdf = gpd.GeoDataFrame(d, crs="EPSG:4326")
gdf = gdf.to_crs('EPSG:23036')
gdf['buffer'] = gdf.geometry.apply(lambda x: x.buffer(50000))
gdf = gdf.set_geometry('buffer')
gdf = gdf.to_crs('EPSG:4326')
bounds = gdf.bounds.loc[0]
north, south, east, west = bounds.maxy, bounds.miny, bounds.minx, bounds.maxx
gdf.loc[1, 'name'] = 'epicenter_rectangle'
gdf.loc[1, 'buffer'] = Polygon(((east,north), (west, north), (west, south), (east, south)))

In [32]:
tags = {'amenity': 'hospital'}

In [ ]:
hospitals = ox.features_from_polygon(gdf.geometry.loc[1], tags=tags)
hospitals.head() # The result is a GeoDataFrame

geometry  \
element_type osmid                                                           
way          323012799   POLYGON ((37.66018 37.79079, 37.66082 37.79013...   
             321950596   POLYGON ((37.15758 38.20408, 37.15762 38.2024,...   
             321950616   POLYGON ((37.18443 38.20627, 37.18452 38.20593...   
             879054113   POLYGON ((37.24591 38.21331, 37.24659 38.21345...   
node         3092021920                           POINT (36.92781 37.5784)   

                                                                     nodes  \
element_type osmid                                                           
way          323012799   [2550330093, 2550330094, 2550330095, 255033009...   
             321950596   [3287180177, 3287180178, 6504350304, 650435030...   
             321950616   [3287184311, 3287184312, 3287184313, 328718431...   
             879054113   [8177780901, 8177780902, 3287649682, 817778090...   
node         3092021920                                                NaN   

                         addr:district   amenity barrier emergency healthcare  \
element_type osmid                                                              
way          323012799         Gölbaşı  hospital    wall       yes   hospital   
             321950596             NaN  hospital     NaN       yes   hospital   
             321950616   Kahramanmaraş  hospital     NaN       NaN   hospital   
             879054113             NaN  hospital     NaN       NaN   hospital   
node         3092021920            NaN  hospital     NaN       NaN   hospital   

                                                  name          operator  \
element_type osmid                                                         
way          323012799        Gölbaşı Devlet Hastanesi  Sağlık Bakanlığı   
             321950596       Elbistan Devlet Hastanesi               NaN   
             321950616   Ozel Elbistan Yasam Hastanesi               NaN   
             879054113                Çiçek Sağlık Evi               NaN   
node         3092021920             Devakent Hastanesi               NaN   

                        operator:wikidata addr:city  check_date  \
element_type osmid                                                
way          323012799           Q4294365       NaN         NaN   
             321950596                NaN  Elbistan         NaN   
             321950616                NaN       NaN  2023-02-07   
             879054113                NaN       NaN         NaN   
node         3092021920               NaN       NaN         NaN   

                                           fixme  \
element_type osmid                                 
way          323012799                       NaN   
             321950596                       NaN   
             321950616   resurvey after recovery   
             879054113                       NaN   
node         3092021920                      NaN   

                                                         note          phone  \
element_type osmid                                                             
way          323012799                                    NaN            NaN   
             321950596                                    NaN            NaN   
             321950616   Battalgazi Mah. Adnan Menderes Bulv.  +903444130303   
             879054113                                    NaN            NaN   
node         3092021920                                   NaN            NaN   

                            source name:en building  
element_type osmid                                   
way          323012799         NaN     NaN      NaN  
             321950596         NaN     NaN      NaN  
             321950616   SafeGraph     NaN      NaN  
             879054113         NaN     NaN      NaN  
node         3092021920        NaN     NaN      NaN

As it is shown, the element type, in this particular case, can be a `way` or a `node`. More information about ways can be found [here](https://wiki.openstreetmap.org/wiki/Way).
The hospitals can be represented as a point or a polygon. 

As it can be seen in the map below, "Afşin Devlet Hastanesi" hospital is being double counted. This is expected due to the nature of the data, crowd sourced. Depending on the usage of the data, one might need to clean the dataset with more or less effort. For example, if the goal is to register all the hospitals that might had been affected, then, double-counting might not be an issue. However, if the goal is to estimate number of affected hospitals, double-counting will need to be eliminated. 

In [34]:
m = folium.Map(location=(38.236801, 36.896292), zoom_start = 15)
hospitals.explore(m = m)

#### Download footprints

In [35]:
# If the goal is to download all the footprints of buildings, one can avoid specifying a tag and use True
tags = {'building': True}
footprints = ox.features_from_polygon(gdf.geometry.loc[1], tags=tags)

In [36]:
footprints.head()

nodes  \
element_type osmid                                                         
way          96356603  [1116696897, 1116695889, 1116699267, 111669386...   
             96356615  [1116697300, 1116698584, 1116697231, 111669474...   
             96356633  [1116697414, 10657820222, 10657820223, 1116696...   
             96356636  [1116696169, 1116694465, 1116698816, 111669747...   
             96356643  [1116696468, 1116695075, 1116699005, 111669768...   

                      building source  \
element_type osmid                      
way          96356603      yes   bing   
             96356615      yes   bing   
             96356633      yes   bing   
             96356636     roof   bing   
             96356643   mosque   bing   

                                                                geometry  \
element_type osmid                                                         
way          96356603  POLYGON ((37.56554 37.7304, 37.56524 37.73063,...   
             96356615  POLYGON ((37.50147 37.5896, 37.50127 37.58934,...   
             96356633  POLYGON ((37.52466 37.79285, 37.52449 37.79282...   
             96356636  POLYGON ((37.50541 37.64448, 37.50507 37.64464...   
             96356643  POLYGON ((37.56499 37.73094, 37.56477 37.73095...   

                      layer           amenity religion denomination name  \
element_type osmid                                                         
way          96356603   NaN               NaN      NaN          NaN  NaN   
             96356615   NaN               NaN      NaN          NaN  NaN   
             96356633   NaN               NaN      NaN          NaN  NaN   
             96356636     1               NaN      NaN          NaN  NaN   
             96356643   NaN  place_of_worship   muslim          NaN  NaN   

                      addr:city  ... stroller roof:colour disused:shop  \
element_type osmid               ...                                     
way          96356603       NaN  ...      NaN         NaN          NaN   
             96356615       NaN  ...      NaN         NaN          NaN   
             96356633       NaN  ...      NaN         NaN          NaN   
             96356636       NaN  ...      NaN         NaN          NaN   
             96356643       NaN  ...      NaN         NaN          NaN   

                      building:levels:underground grades name:nl loc_name  \
element_type osmid                                                          
way          96356603                         NaN    NaN     NaN      NaN   
             96356615                         NaN    NaN     NaN      NaN   
             96356633                         NaN    NaN     NaN      NaN   
             96356636                         NaN    NaN     NaN      NaN   
             96356643                         NaN    NaN     NaN      NaN   

                       fee house operator:short  
element_type osmid                               
way          96356603  NaN   NaN            NaN  
             96356615  NaN   NaN            NaN  
             96356633  NaN   NaN            NaN  
             96356636  NaN   NaN            NaN  
             96356643  NaN   NaN            NaN  

[5 rows x 125 columns]

In [37]:
print('With OSM {} buildings were downloaded'.format(len(footprints)))

With OSM 160180 buildings were downloaded


In [38]:
footprints.amenity.value_counts()

amenity
place_of_worship    402
school               13
library               8
police                8
community_centre      7
clinic                6
restaurant            6
bank                  6
townhall              5
cafe                  5
public_building       5
marketplace           4
car_wash              3
parking               3
courthouse            2
toilets               2
bus_station           2
food_court            2
public_bath           2
social_facility       1
mosque                1
hospital              1
theatre               1
dentist               1
prison                1
fire_station          1
Name: count, dtype: int64

In [39]:
footprints.head(1000).explore()

Let's explore the limitations of this data with an example. When downloading all the amenities tagged as `restaurant`, only 17 places are found. It seems unlikely that there are 17 restaurants in the entire region. So, it is worth querying all the amenities. Unfortunately, the result is the same and the quality of the data for restaurants is not good. 

In [40]:
tags = {'amenity': 'restaurant'}
restaurant = ox.features_from_polygon(gdf.geometry.loc[1], tags=tags)

In [41]:
len(restaurant)

17

In [42]:
tags = {'amenity': True}
amenities = ox.features_from_polygon(gdf.geometry.loc[1], tags=tags)

In [43]:
amenities['amenity'].value_counts()

amenity
place_of_worship    405
pharmacy            224
school              212
fuel                133
parking              80
bank                 58
cafe                 40
clinic               26
hospital             20
atm                  17
restaurant           17
drinking_water       15
waste_disposal       11
food_court           11
police               10
library              10
marketplace           9
toilets               8
kindergarten          8
community_centre      7
townhall              6
car_wash              6
fast_food             6
university            6
public_building       5
social_facility       4
post_office           3
dentist               3
taxi                  3
water_point           3
public_bath           2
fire_station          2
cinema                2
courthouse            2
theatre               2
social_centre         2
prison                2
bus_station           2
refugee_site          2
vending_machine       2
shelter               2
bicycle_

### Discussion
- What do you think about this dataset?
- In which crisis related task will it become handy?
- Do you see any other limitation? 
- Which are your proposals to clean this type of data? 

#### Note
OSM data can be downloaded in other ways as well, for example using QGIS or even ChatGPT. This course decided to use OSMnx, as it more flexible. 

### HOT Export Tool

[HOT](https://www.hotosm.org/what-we-do) is an international team dedicated to humanitarian action and community development through open mapping. They work together to provide map data which revolutionizes disaster management, reduces risks, and contributes to achievement of the Sustainable Development Goals.

The [Export Tool](https://export.hotosm.org/v3/) is an open service that creates customized extracts of up-to-date OSM data in various file formats. This allows users to download the necessary data for a region of interest without requiring coding experience. Below, we show the 4 steps to obtain the data with this tool. 

```{figure} ../images/hot_step1.png
---
width: 800
name: HOT step 1
---
Project definition.
```
```{figure} ../images/hot_step2.png
---
width: 800
name: HOT step 2
---
Define the extension of the output file.
```
```{figure} ../images/hot_step3.png
---
width: 800
name: HOT step 3
---
Select the data you want to export.
```
```{figure} ../images/hot_step4.png
---
width: 800
name: HOT step 4
---
Define your area of interest and export.
``` 